In [ ]:
import argparse
import os, sys
import time
import datetime
from tqdm import tqdm_notebook as tqdm

import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim
from torch.optim.lr_scheduler import StepLR
from torch.utils.data import DataLoader
import torchvision
import torchvision.transforms as transforms
import numpy as np
from tools.dataset import CIFAR10
from torch.utils.data import DataLoader
import math
import torchvision.models as models

In [ ]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

In [ ]:
transform_train = transforms.Compose([
    transforms.ToTensor(),
    transforms.Normalize((0.4914, 0.4822, 0.4465), (0.2023, 0.1994, 0.2010)),
])

transform_test = transforms.Compose([
    transforms.ToTensor(),
    transforms.Normalize((0.4914, 0.4822, 0.4465), (0.2023, 0.1994, 0.2010)),
])

In [ ]:
batch_size = 512

In [ ]:
from tools.dataset import CIFAR10
from torch.utils.data import DataLoader

# a few arguments, do NOT change these
DATA_ROOT = "./data"
TRAIN_BATCH_SIZE = batch_size
TEST_BATCH_SIZE = 100

#############################################
# your code here
# construct dataset
train_set = CIFAR10(
    root=DATA_ROOT,
    mode='train',
    download=True,
    transform=transform_train    # your code
)
val_set = CIFAR10(
    root=DATA_ROOT,
    mode='val',
    download=True,
    transform=transform_test    # your code
)

# construct dataloader
train_loader = DataLoader(
    train_set,
    batch_size=TRAIN_BATCH_SIZE,  # your code
    shuffle=True,     # your code
    num_workers=4
)
val_loader = DataLoader(
    val_set,
    batch_size=TEST_BATCH_SIZE,  # your code
    shuffle=True,     # your code
    num_workers=4
)
#############################################

Using downloaded and verified file: ./data/cifar10_trainval_F22.zip
Extracting ./data/cifar10_trainval_F22.zip to ./data
Files already downloaded and verified
Using downloaded and verified file: ./data/cifar10_trainval_F22.zip
Extracting ./data/cifar10_trainval_F22.zip to ./data
Files already downloaded and verified


In [1]:
## Code for CNN architectures from original RotNet paper: https://github.com/gidariss/FeatureLearningRotNet

class BasicBlock(nn.Module):
    def __init__(self, in_planes, out_planes, kernel_size, stride=1):
        super(BasicBlock, self).__init__()
        padding = int((kernel_size-1)/2)
        self.layers = nn.Sequential()
        self.layers.add_module('Conv', nn.Conv2d(in_planes, out_planes, \
            kernel_size=kernel_size, stride=stride, padding=padding, bias=False))
        self.layers.add_module('BatchNorm', nn.BatchNorm2d(out_planes))
        self.layers.add_module('ReLU',      nn.ReLU(inplace=True))

    def forward(self, x):
        return self.layers(x)

class GlobalAvgPool(nn.Module):
    def __init__(self):
        super(GlobalAvgPool, self).__init__()

    def forward(self, feat):
        assert(feat.size(2) == feat.size(3))
        feat_avg = F.avg_pool2d(feat, feat.size(2)).view(-1, feat.size(1))
        return feat_avg

class Flatten(nn.Module):
    def __init__(self):
        super(Flatten, self).__init__()

    def forward(self, feat):
        return feat.view(feat.size(0), -1)

class GlobalAveragePooling(nn.Module):
    def __init__(self):
        super(GlobalAveragePooling, self).__init__()

    def forward(self, feat):
        num_channels = feat.size(1)
        return F.avg_pool2d(feat, (feat.size(2), feat.size(3))).view(-1, num_channels)


# classifier to train on images
class NonLinearClassifier(nn.Module):
    def __init__(self):
        super(NonLinearClassifier, self).__init__()
        nChannels      = 192
        num_classes    = 10

        self.classifier = nn.Sequential()

        self.classifier.add_module('Block3_ConvB1',  BasicBlock(nChannels, 192, 3))
        self.classifier.add_module('Block3_ConvB2',  BasicBlock(192, 192, 1))
        self.classifier.add_module('Block3_ConvB3',  BasicBlock(192, 192, 1))
        self.classifier.add_module('GlobalAvgPool',  GlobalAvgPool())
        self.classifier.add_module('Liniear_F',      nn.Linear(192, num_classes))

        self.initilize()

    def forward(self, feat):
        return self.classifier(feat)

    def initilize(self):
        for m in self.modules():
            if isinstance(m, nn.Conv2d):
                n = m.kernel_size[0] * m.kernel_size[1] * m.out_channels
                m.weight.data.normal_(0, math.sqrt(2. / n))
            elif isinstance(m, nn.BatchNorm2d):
                m.weight.data.fill_(1)
                m.bias.data.zero_()
            elif isinstance(m, nn.Linear):
                fin = m.in_features
                fout = m.out_features
                std_val = np.sqrt(2.0/fout)
                m.weight.data.normal_(0.0, std_val)
                if m.bias is not None:
                    m.bias.data.fill_(0.0)

# rotation classifier
class NetworkInNetwork(nn.Module):
    def __init__(self):
        super(NetworkInNetwork, self).__init__()

        num_classes = 4
        num_inchannels = 3
        num_stages = 4

        nChannels  = 192
        nChannels2 = 160
        nChannels3 = 96

        blocks = [nn.Sequential() for i in range(4)]
        # 1st block
        blocks[0].add_module('Block1_ConvB1', BasicBlock(num_inchannels, nChannels, 5))
        blocks[0].add_module('Block1_ConvB2', BasicBlock(nChannels,  nChannels2, 1))
        blocks[0].add_module('Block1_ConvB3', BasicBlock(nChannels2, nChannels3, 1))
        blocks[0].add_module('Block1_MaxPool', nn.MaxPool2d(kernel_size=3,stride=2,padding=1))

        # 2nd block
        blocks[1].add_module('Block2_ConvB1',  BasicBlock(nChannels3, nChannels, 5))
        blocks[1].add_module('Block2_ConvB2',  BasicBlock(nChannels,  nChannels, 1))
        blocks[1].add_module('Block2_ConvB3',  BasicBlock(nChannels,  nChannels, 1))
        blocks[1].add_module('Block2_AvgPool', nn.AvgPool2d(kernel_size=3,stride=2,padding=1))

        # 3rd block
        blocks[2].add_module('Block3_ConvB1',  BasicBlock(nChannels, nChannels, 3))
        blocks[2].add_module('Block3_ConvB2',  BasicBlock(nChannels, nChannels, 1))
        blocks[2].add_module('Block3_ConvB3',  BasicBlock(nChannels, nChannels, 1))
        # blocks[2].add_module('Block3_AvgPool', nn.AvgPool2d(kernel_size=3,stride=2,padding=1))

        # 4th block
        blocks[3].add_module('Block4_ConvB1',  BasicBlock(nChannels, nChannels, 3))
        blocks[3].add_module('Block4_ConvB2',  BasicBlock(nChannels, nChannels, 1))
        blocks[3].add_module('Block4_ConvB3',  BasicBlock(nChannels, nChannels, 1))

        # end classifier
        blocks.append(nn.Sequential())
        blocks[-1].add_module('GlobalAveragePooling',  GlobalAveragePooling())
        blocks[-1].add_module('Classifier', nn.Linear(nChannels, num_classes))

        self._feature_blocks = nn.ModuleList(blocks)

    def forward(self, x):
        """Forward an image `x` through the network and return the asked output features.

        Args:
          x: input image.
          out_feat_keys: a list/tuple with the feature names of the features
                  that the function should return. By default the last feature of
                  the network is returned.

        Return:
              out_feats: If multiple output features were asked then `out_feats`
                  is a list with the asked output features placed in the same
                  order as in `out_feat_keys`. If a single output feature was
                  asked then `out_feats` is that output feature (and not a list).
        """
        for block in self._feature_blocks[:-1]:  # Pass through all blocks except the classifier
          x = block(x)
        x = self._feature_blocks[-1](x)  # Pass through the classifier block
        return x

NameError: ignored

In [ ]:
# return tensor of shape (4*batch size, 3, 32, 32)
def rotate_tensor_four_times(tensor):

    rotated_tensors = []
    rotated_tensors.append(tensor) # 0 degrees
    rotated_tensors.append(torch.rot90(tensor, k=1, dims=(2, 3))) # 90 degrees
    rotated_tensors.append(torch.rot90(tensor, k=2, dims=(2, 3))) # 180 degrees
    rotated_tensors.append(torch.rot90(tensor, k=3, dims=(2, 3))) # 270 degrees

    return torch.cat(rotated_tensors, dim=0).to(device)

In [ ]:
class RotNetLoss(nn.Module):
    def __init__(self, num_classes=4):
        super().__init__()
        self.num_classes = num_classes
        self.cross_entropy = nn.CrossEntropyLoss()

    def forward(self, predictions):
        batch_size = int(predictions.shape[0] / 4)

        targets = []
        labels = []
        for i in range(self.num_classes):
          for j in range(batch_size):
            targets.append(i)
            inner_list = []
            for inner_i in range(self.num_classes):
              inner_list.append(i==inner_i)
            labels.append(inner_list)

        labels = torch.tensor(labels, dtype=torch.float32).to(device)
        targets = torch.tensor(targets, dtype=torch.float32).to(device)
        return self.cross_entropy(predictions, labels), targets

In [ ]:
def create_train_finetune(train_batch):
  DATA_ROOT = "./data"
  TRAIN_BATCH_SIZE = train_batch
  transform_train = transforms.Compose([
      transforms.RandomCrop(32, padding=4),
      transforms.RandomHorizontalFlip(),
      transforms.ToTensor(),
      transforms.Normalize((0.4914, 0.4822, 0.4465), (0.2023, 0.1994, 0.2010))
  ])
  # construct dataset
  train_set = CIFAR10(
      root=DATA_ROOT,
      mode='train',
      download=True,
      transform=transform_train
  )
  # construct dataloader
  train_loader = DataLoader(
      train_set,
      batch_size=TRAIN_BATCH_SIZE,
      shuffle=True,
      num_workers=4
  )
  return train_loader

In [ ]:
# other arguments
model_checkpoint = 'rotnet_model'

# hyperparameters
batch_size = batch_size
momentum = 0.9
weight_decay = 5 * 10**-4
lr = 0.1
lr_decay_rate = 0.2
lr_decay_epochs = [29,59,79]
total_epochs = 100

# initialize net
net = NetworkInNetwork()
net = net.to(device)

# loss and optimizer
criterion = RotNetLoss(num_classes=4)
optimizer = optim.SGD(net.parameters(), lr=lr, nesterov=True, momentum=momentum, weight_decay=weight_decay)


print("Start training")
best_val_acc = 0
for epoch in range(total_epochs):
  print("Epoch {}".format(epoch))
  # Adjust learning rate
  if epoch in lr_decay_epochs:
    lr *= lr_decay_rate
    for param_group in optimizer.param_groups:
      param_group['lr'] = lr
    print("LR decayed")

  # Wrap the train_loader with tqdm for a progress bar
  total_loss = 0
  total = 0
  correct = 0
  net.train()
  progress_bar = tqdm(enumerate(train_loader), total=len(train_loader), desc=f"Epoch {epoch+1}/{total_epochs}", leave=False)
  for batch_idx, (inputs, _) in progress_bar:  # targets are not used in SimCLR

      # make sure inputs are on device
      inputs = inputs.to(device)

      # get tensor of rotated inputs (4*batch size, 3, 32, 32)
      rotated_inputs = rotate_tensor_four_times(inputs)

      # forward pass
      predictions = net.forward(rotated_inputs)

      # calculate loss
      loss, targets = criterion.forward(predictions)

      # update optimizer and loss
      optimizer.zero_grad()
      loss.backward()
      optimizer.step()

      # for progresss bar
      total_loss += loss.item()
      progress_bar.set_postfix(loss=total_loss / (batch_idx + 1))

      _, predicted = torch.max(predictions.data, 1)
      total += targets.size(0)
      correct += (predicted == targets).sum().item()

  progress_bar.close()

  print(correct/total)

  net.eval()
  with torch.no_grad():
    for batch_idx, (inputs, targets) in enumerate(val_loader):

      # make sure inputs are on device
      inputs = inputs.to(device)

      # get tensor of rotated inputs (4*batch size, 3, 32, 32)
      rotated_inputs = rotate_tensor_four_times(inputs)

      # forward pass
      predictions = net.forward(rotated_inputs)

      # calculate loss
      loss, targets = criterion.forward(predictions)

      _, predicted = torch.max(predictions.data, 1)
      total += targets.size(0)
      correct += (predicted == targets).sum().item()

  avg_acc = correct / total
  print("validation accuracy: %.4f" % (avg_acc))

  # save the model checkpoint
  if avg_acc > best_val_acc:
      best_val_acc = avg_acc

      # save net
      torch.save(net.state_dict(), "rotnet_epoch{}_batch{}".format(epoch, str(batch_size)))

Start training
Epoch 0


<ipython-input-38-8f86dd598be4>:38: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`
  progress_bar = tqdm(enumerate(train_loader), total=len(train_loader), desc=f"Epoch {epoch+1}/{total_epochs}", leave=False)


Epoch 1/100:   0%|          | 0/88 [00:00<?, ?it/s]

0.6052833333333333
validation accuracy: 0.5942
Epoch 1


Epoch 2/100:   0%|          | 0/88 [00:00<?, ?it/s]

...

1.0
validation accuracy: 0.9896
Epoch 42


Epoch 43/100:   0%|          | 0/88 [00:00<?, ?it/s]

1.0
validation accuracy: 0.9895
Epoch 43


Epoch 44/100:   0%|          | 0/88 [00:00<?, ?it/s]

KeyboardInterrupt: ignored

In [ ]:
def fine_tune(net, train_loader, val_loader, device, total_epochs, model_checkpoint_net):


  optimizer_net = optim.SGD(list(net.parameters()), lr=0.01, weight_decay=1e-6,
                              momentum=0.9)

  best_val_acc = 0
  for epoch in range(total_epochs):
      net.train()
      # Adjust learning rate
      #cosine_decay_learning_rate(epoch, total_epochs, warmup_epochs, base_lr, optimizer)

      print("Epoch %d:", epoch)
      # this help you compute the training accuracy
      total_examples = 0
      correct_examples = 0

      total_loss = 0

      progress_bar = tqdm(enumerate(train_loader), total=len(train_loader), desc=f"Epoch {epoch+1}/{total_epochs}", leave=False)
      for batch_idx, (inputs, targets) in progress_bar:  # targets are not used in SimCLR
          inputs = inputs.to(device)
          targets = targets.to(device)
          net.to(device)

          output = net(inputs)
          loss = F.cross_entropy(output, targets)

          total_loss += loss.item()

          # zero the gradient
          optimizer_net.zero_grad()
          # backpropagation
          loss.backward()

          # apply gradient and update the weights
          optimizer_net.step()
          # count the number of correctly predicted samples in the current batch

          predicted_classes = output.max(1)[1] # get most probable class for each predictions (max within column(class))
          total_examples += targets.size(0)
          equality_comparison = predicted_classes.eq(targets) # compare if each prediciton is correct
          correct_examples += equality_comparison.sum().item() # add trues from above to num of correct predictions (looked this up online)


          #total_loss += loss.item()
          progress_bar.set_postfix(loss=total_loss / (batch_idx + 1))

      progress_bar.close()

      avg_loss = total_loss / len(train_loader)
      avg_acc = correct_examples / total_examples
      print("Training loss: %.4f, Training accuracy: %.4f" %(avg_loss, avg_acc))

      # Validate on the validation dataset
      #######################
      # your code here
      # switch to eval mode
      net.eval()

      #######################

      # this help you compute the validation accuracy
      total_examples = 0
      correct_examples = 0

      val_loss = 0 # again, track the validation loss if you want

          # disable gradient during validation, which can save GPU memory
      with torch.no_grad():
          for batch_idx, (inputs, targets) in enumerate(val_loader):
              ####################################
              # your code here
              # copy inputs to device
              inputs = inputs.to(device)
              targets = targets.to(device)

              # compute the output and loss
              output = net(inputs)
              loss = F.cross_entropy(output, targets)
              val_loss += loss.item()

              # count the number of correctly predicted samples in the current batch
              predicted_classes = output.max(1)[1] # get most probable class for each prediction
              total_examples += targets.size(0)
              equality_comparison = predicted_classes.eq(targets) # compare if each prediciton is correct
              correct_examples += equality_comparison.sum().item() # add trues from above to num of correct predictions

              ####################################

      avg_loss = val_loss / len(val_loader)
      avg_acc = correct_examples / total_examples
      print("Validation loss: %.4f, Validation accuracy: %.4f" % (avg_loss, avg_acc))

      # save the model checkpoint
      if avg_acc > best_val_acc:
          best_val_acc = avg_acc

          torch.save(net.state_dict(), model_checkpoint_net)

      print('')


  print(f"==> Optimization finished! Best validation accuracy: {best_val_acc:.4f}")

In [ ]:
total_epochs = 100
model_checkpoint_net = 'fine_tuned_model5'

net = NetworkInNetwork()
net.load_state_dict(torch.load("rotnet_epoch0_batch{}".format(str(batch_size))))
# freeze first two blocks
for i, block in enumerate(net._feature_blocks[:-1]):
    if i < 2:  # Freeze the first two blocks
        for param in block.parameters():
            param.requires_grad = False
net._feature_blocks[2] = nn.Sequential()
net._feature_blocks[3] = nn.Sequential()
net._feature_blocks[4] = NonLinearClassifier()

fine_tune(net, create_train_finetune(batch_size), val_loader, device, total_epochs, model_checkpoint_net)

Using downloaded and verified file: ./data/cifar10_trainval_F22.zip
Extracting ./data/cifar10_trainval_F22.zip to ./data
Files already downloaded and verified
Epoch %d: 0


<ipython-input-27-9016f68c6fb5>:20: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`
  progress_bar = tqdm(enumerate(train_loader), total=len(train_loader), desc=f"Epoch {epoch+1}/{total_epochs}", leave=False)


Epoch 1/100:   0%|          | 0/176 [00:00<?, ?it/s]

Training loss: 1.4872, Training accuracy: 0.5028
Validation loss: 1.1975, Validation accuracy: 0.5724

Epoch %d: 1


Epoch 2/100:   0%|          | 0/176 [00:00<?, ?it/s]

...

Training loss: 0.3033, Training accuracy: 0.8932
Validation loss: 0.9498, Validation accuracy: 0.7418

Epoch %d: 98


Epoch 99/100:   0%|          | 0/176 [00:00<?, ?it/s]

Training loss: 0.3028, Training accuracy: 0.8932
Validation loss: 0.9019, Validation accuracy: 0.7526

Epoch %d: 99


Epoch 100/100:   0%|          | 0/176 [00:00<?, ?it/s]

Training loss: 0.3017, Training accuracy: 0.8928
Validation loss: 1.0145, Validation accuracy: 0.7404

==> Optimization finished! Best validation accuracy: 0.7666


In [ ]:
total_epochs = 100
model_checkpoint_net = 'fine_tuned_model_train0'

net = NetworkInNetwork()
net.load_state_dict(torch.load("rotnet_epoch0_batch128"))
# freeze first two blocks
for i, block in enumerate(net._feature_blocks[:-1]):
    if i < 2:  # Freeze the first two blocks
        for param in block.parameters():
            param.requires_grad = False
net._feature_blocks[2] = nn.Sequential()
net._feature_blocks[3] = nn.Sequential()
net._feature_blocks[4] = NonLinearClassifier()

fine_tune(net, create_train_finetune(128), val_loader, device, total_epochs, model_checkpoint_net)

Using downloaded and verified file: ./data/cifar10_trainval_F22.zip
Extracting ./data/cifar10_trainval_F22.zip to ./data
Files already downloaded and verified
Epoch %d: 0


<ipython-input-11-9016f68c6fb5>:20: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`
  progress_bar = tqdm(enumerate(train_loader), total=len(train_loader), desc=f"Epoch {epoch+1}/{total_epochs}", leave=False)


Epoch 1/100:   0%|          | 0/352 [00:00<?, ?it/s]

Training loss: 1.2692, Training accuracy: 0.5634
Validation loss: 1.0453, Validation accuracy: 0.6260

Epoch %d: 1


Epoch 2/100:   0%|          | 0/352 [00:00<?, ?it/s]

...

Training loss: 0.2325, Training accuracy: 0.9178
Validation loss: 0.8263, Validation accuracy: 0.7900

Epoch %d: 98


Epoch 99/100:   0%|          | 0/352 [00:00<?, ?it/s]

Training loss: 0.2292, Training accuracy: 0.9166
Validation loss: 0.7456, Validation accuracy: 0.7980

Epoch %d: 99


Epoch 100/100:   0%|          | 0/352 [00:00<?, ?it/s]

Training loss: 0.2325, Training accuracy: 0.9184
Validation loss: 0.8106, Validation accuracy: 0.7896

==> Optimization finished! Best validation accuracy: 0.7986


In [ ]:
total_epochs = 100
model_checkpoint_net = 'fine_tuned_model_train25'

net = NetworkInNetwork()
net.load_state_dict(torch.load("rotnet_epoch22_batch5"))
# freeze first two blocks
for i, block in enumerate(net._feature_blocks[:-1]):
    if i < 2:  # Freeze the first two blocks
        for param in block.parameters():
            param.requires_grad = False
net._feature_blocks[2] = nn.Sequential()
net._feature_blocks[3] = nn.Sequential()
net._feature_blocks[4] = NonLinearClassifier()

fine_tune(net, create_train_finetune(512), val_loader, device, total_epochs, model_checkpoint_net)

Using downloaded and verified file: ./data/cifar10_trainval_F22.zip
Extracting ./data/cifar10_trainval_F22.zip to ./data
Files already downloaded and verified
Epoch %d: 0


<ipython-input-11-9016f68c6fb5>:20: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`
  progress_bar = tqdm(enumerate(train_loader), total=len(train_loader), desc=f"Epoch {epoch+1}/{total_epochs}", leave=False)


Epoch 1/100:   0%|          | 0/88 [00:00<?, ?it/s]

Training loss: 1.3070, Training accuracy: 0.5642
Validation loss: 0.9160, Validation accuracy: 0.6814

Epoch %d: 1


Epoch 2/100:   0%|          | 0/88 [00:00<?, ?it/s]

...

Training loss: 0.1301, Training accuracy: 0.9561
Validation loss: 0.5620, Validation accuracy: 0.8498

Epoch %d: 98


Epoch 99/100:   0%|          | 0/88 [00:00<?, ?it/s]

Training loss: 0.1274, Training accuracy: 0.9586
Validation loss: 0.5941, Validation accuracy: 0.8386

Epoch %d: 99


Epoch 100/100:   0%|          | 0/88 [00:00<?, ?it/s]

Training loss: 0.1264, Training accuracy: 0.9576
Validation loss: 0.5850, Validation accuracy: 0.8386

==> Optimization finished! Best validation accuracy: 0.8530


In [1]:
total_epochs = 100
model_checkpoint_net = 'fine_tuned_model_train50'

net = NetworkInNetwork()
net.load_state_dict(torch.load("rotnet_epoch39_batch512"))
# freeze first two blocks
for i, block in enumerate(net._feature_blocks[:-1]):
    if i < 2:  # Freeze the first two blocks
        for param in block.parameters():
            param.requires_grad = False
net._feature_blocks[2] = nn.Sequential()
net._feature_blocks[3] = nn.Sequential()
net._feature_blocks[4] = NonLinearClassifier()


## code below for nonlinear classifier
# Add new classifier as third block
# nChannels      = 192*8*8
# num_classes    = 10
# new_block = nn.Sequential()
# nFeats = min(200, 2048)
# new_block.add_module('Flatten',     Flatten())
# new_block.add_module('Liniear_1',   nn.Linear(nChannels, nFeats, bias=False))
# new_block.add_module('BatchNorm_1', nn.BatchNorm1d(nFeats))
# new_block.add_module('ReLU_1',      nn.ReLU(inplace=True))
# new_block.add_module('Liniear_2',   nn.Linear(nFeats, nFeats, bias=False))
# new_block.add_module('BatchNorm2d', nn.BatchNorm1d(nFeats))
# new_block.add_module('ReLU_2',      nn.ReLU(inplace=True))
# new_block.add_module('Liniear_F',   nn.Linear(nFeats, num_classes))
# model._feature_blocks[2] = new_block
# model._feature_blocks[3] = nn.Sequential()
# model._feature_blocks[4] = nn.Sequential()

fine_tune(net, create_train_finetune(512), val_loader, device, total_epochs, model_checkpoint_net)

NameError: ignored

In [ ]:
total_epochs = 100
model_checkpoint_net = 'fine_tuned_model_train100'

net = NetworkInNetwork()
net.load_state_dict(torch.load("rotnet_epoch39_batch512"))
# freeze first two blocks
for i, block in enumerate(net._feature_blocks[:-1]):
    if i < 2:  # Freeze the first two blocks
        for param in block.parameters():
            param.requires_grad = False
net._feature_blocks[2] = nn.Sequential()
net._feature_blocks[3] = nn.Sequential()
net._feature_blocks[4] = NonLinearClassifier()

fine_tune(net, create_train_finetune(512), val_loader, device, total_epochs, model_checkpoint_net)

Using downloaded and verified file: ./data/cifar10_trainval_F22.zip
Extracting ./data/cifar10_trainval_F22.zip to ./data
Files already downloaded and verified
Epoch %d: 0


<ipython-input-11-9016f68c6fb5>:20: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`
  progress_bar = tqdm(enumerate(train_loader), total=len(train_loader), desc=f"Epoch {epoch+1}/{total_epochs}", leave=False)


Epoch 1/100:   0%|          | 0/88 [00:00<?, ?it/s]

Training loss: 1.2946, Training accuracy: 0.5717
Validation loss: 0.9008, Validation accuracy: 0.6816

Epoch %d: 1


Epoch 2/100:   0%|          | 0/88 [00:00<?, ?it/s]

...

Training loss: 0.1209, Training accuracy: 0.9606
Validation loss: 0.5355, Validation accuracy: 0.8544

Epoch %d: 98


Epoch 99/100:   0%|          | 0/88 [00:00<?, ?it/s]

Training loss: 0.1205, Training accuracy: 0.9596
Validation loss: 0.5681, Validation accuracy: 0.8510

Epoch %d: 99


Epoch 100/100:   0%|          | 0/88 [00:00<?, ?it/s]

Training loss: 0.1203, Training accuracy: 0.9604
Validation loss: 0.5599, Validation accuracy: 0.8506

==> Optimization finished! Best validation accuracy: 0.8584
